### Just a playground for extracting geolocations from text

In [50]:
# Get the Scroll ID
import sys
import csv
from elasticsearch import Elasticsearch
es = Elasticsearch()

count = 10000
geo_file = "geonames_all.csv"

In [51]:
doc = {
    'size' : count,
    "_source": ["coordinates", "asciiname", "name", "alternativenames"],
    "query":{
        "type" : {
            "value" : "geoname"
        }
    }
}

with open(geo_file, mode='w') as csv_file:
    fieldnames = ['id','coordinates','asciiname', "name", "alternativenames"]
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
    writer.writeheader()

    response = es.search(index="geonames", doc_type='geoname', body=doc ,scroll='1m')
    scroll = response['_scroll_id']
    print("Scroll ID %s" % scroll)

#     orig_stdout = sys.stdout
#     f = open(geo_file, 'w')
#     sys.stdout = f
#     print("id,coordinates,asciiname") # print header

    #print first 10000
    for hit in response['hits']['hits']:
#         print("%s,\"%s\",\"%s\"" % (hit['_id'],hit['_source']['coordinates'],hit['_source']['asciiname']))
        writer.writerow({'id':hit['_id'], 'coordinates':hit['_source']['coordinates'], 'asciiname':hit['_source']['asciiname'], 'name':hit['_source']['name'], 'alternativenames':hit['_source']['alternativenames']})

    #Now use the scroll is to get the rest of the records
    while count < 11741135:  
        response = es.scroll(scroll_id = scroll, scroll = '1m')
        for hit in response['hits']['hits']:
#             print("%s,\"%s\",\"%s\"" % (hit['_id'],hit['_source']['coordinates'],hit['_source']['asciiname']))
            writer.writerow({'id':hit['_id'], 'coordinates':hit['_source']['coordinates'], 'asciiname':hit['_source']['asciiname'], 'name':hit['_source']['name'], 'alternativenames':hit['_source']['alternativenames']})


        count += 10000

#     sys.stdout = orig_stdout
#     f.close()  

    # Done outputting records!
    print("Done")

#500M Large!

Scroll ID DXF1ZXJ5QW5kRmV0Y2gBAAAAAAACzBYWaU02aUZNOVlRMmk0ZTVDcDJFTlhmZw==
Done


In [4]:
import pandas as pd

df = pd.read_csv(geo_file)
print(df.shape)

(11741135, 3)


In [5]:
import sys; sys.executable

'/usr/local/opt/python/bin/python3.6'

In [6]:
import spacy
nlp = spacy.load('en_core_web_lg')

In [3]:
from mordecai import Geoparser
geo = Geoparser()
geo.geoparse("I traveled from Oxford to Ottawa.")

Using TensorFlow backend.


[{'word': 'Oxford',
  'spans': [{'start': 16, 'end': 22}],
  'country_predicted': 'GBR',
  'country_conf': 0.96474487,
  'geo': {'admin1': 'England',
   'lat': '51.75222',
   'lon': '-1.25596',
   'country_code3': 'GBR',
   'geonameid': '2640729',
   'place_name': 'Oxford',
   'feature_class': 'P',
   'feature_code': 'PPLA2'}},
 {'word': 'Ottawa',
  'spans': [{'start': 26, 'end': 32}],
  'country_predicted': 'CAN',
  'country_conf': 0.83302397,
  'geo': {'admin1': 'Ontario',
   'lat': '45.41117',
   'lon': '-75.69812',
   'country_code3': 'CAN',
   'geonameid': '6094817',
   'place_name': 'Ottawa',
   'feature_class': 'P',
   'feature_code': 'PPLC'}}]

In [15]:
%%time
#Evaluate
missed = []
achieved = []

count = 0
for index, row in df.iterrows():
    #lets parse each locations!
    #print(row['asciiname'])
    res = geo.geoparse(row['asciiname'])
    if res:
        achieved.append(row['asciiname'])
    else:
        missed.append(row['asciiname'])
    
    if count % 10000 == 0:
        print("Completed %s records" % count)
    count += 1
    
print("Finally Done!")
print("%s/11741135 achieved" % len(achieved))
print("%s/11741135 missed" % len(missed))
#11,741,135 -> This will take a long time...

Completed 0 records
Completed 10000 records
Completed 20000 records
Completed 30000 records
Completed 40000 records
Completed 50000 records
Completed 60000 records
Completed 70000 records
Completed 80000 records
Completed 90000 records
Completed 100000 records
Completed 110000 records
Completed 120000 records
Completed 130000 records
Completed 140000 records
Completed 150000 records
Completed 160000 records
Completed 170000 records
Completed 180000 records
Completed 190000 records
Completed 200000 records
Completed 210000 records
Completed 220000 records
Completed 230000 records
Completed 240000 records
Completed 250000 records
Completed 260000 records
Completed 270000 records
Completed 280000 records
Completed 290000 records
Completed 300000 records
Completed 310000 records
Completed 320000 records
Completed 330000 records
Completed 340000 records
Completed 350000 records
Completed 360000 records
Completed 370000 records
Completed 380000 records
Completed 390000 records
Completed 4000

KeyboardInterrupt: 

In [16]:
print("%s/11741135 achieved" % len(achieved))
print("%s/11741135 missed" % len(missed))

130501/11741135 achieved
1065910/11741135 missed


In [27]:
%%time
#Try World Locations (Context + Uppercase)

q = ["Where is "]

wl_got = []
wl_missed = []

c = 0
with open("../Rasa/roger_nlu/location_data/world_locations_ed2.txt", 'r') as wlf:
    print("file open")
    line = wlf.readline()
    while line:
        res = geo.geoparse("%s%s" % (q,line.strip()))
        if res:
            wl_got.append(line.strip())
        else:
            wl_missed.append(line.strip())
        line = wlf.readline()
        c += 1
        
        if c % 1000 == 0:
            print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

file open
Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000

In [28]:
%%time
#Try World Locations (Context + lowercase)

q = ["Where is "]

wl_got = []
wl_missed = []

c = 0
with open("../Rasa/roger_nlu/location_data/world_locations.txt", 'r') as wlf:
    print("file open")
    line = wlf.readline()
    while line:
        res = geo.geoparse("%s%s" % (q,line.strip()))
        if res:
            wl_got.append(line.strip())
        else:
            wl_missed.append(line.strip())
        line = wlf.readline()
        c += 1
        
        if c % 1000 == 0:
            print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

file open
Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000

In [30]:
%%time
#Try World Locations (lowercase)

wl_got = []
wl_missed = []

c = 0
with open("../Rasa/roger_nlu/location_data/world_locations.txt", 'r') as wlf:
    print("file open")
    line = wlf.readline()
    while line:
        res = geo.geoparse("%s" % (line.strip()))
        if res:
            wl_got.append(line.strip())
        else:
            wl_missed.append(line.strip())
        line = wlf.readline()
        c += 1
        
        if c % 1000 == 0:
            print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

file open
Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000

In [31]:
%%time
#Try World Locations (uppercase)

wl_got = []
wl_missed = []

c = 0
with open("../Rasa/roger_nlu/location_data/world_locations_ed2.txt", 'r') as wlf:
    print("file open")
    line = wlf.readline()
    while line:
        res = geo.geoparse("%s" % (line.strip()))
        if res:
            wl_got.append(line.strip())
        else:
            wl_missed.append(line.strip())
        line = wlf.readline()
        c += 1
        
        if c % 1000 == 0:
            print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

file open
Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000

In [25]:
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

Finally Done!
2593/3064 achieved
471/3064 missed


In [4]:
import json
def read_locations(filename, loc_type):
    list1 = []
    with open(filename,'r') as f:
        data = json.load(f)
    temp = data[loc_type]
    for item in temp:
        location = item['name']
        list1.append(location)
    return list1
countries = read_locations('../Rasa/roger_nlu/location_data/countries.json',"countries")
states = read_locations('../Rasa/roger_nlu/location_data/states.json',"states")
cities = read_locations('../Rasa/roger_nlu/location_data/cities.json', "cities")

all_locs = countries + states + cities

#List
print(len(all_locs))
#iterate through

52709


In [40]:
#Try Individual Locations (uppercase)
wl_got = []
wl_missed = []

c = 0
for loc in all_locs:
    res = geo.geoparse("%s" % (loc))
    if res:
        wl_got.append(loc)
    else:
        wl_missed.append(loc)
    c += 1

    if c % 1000 == 0:
        print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000 records
C

In [41]:
#Try Individual Locations (uppercase with context)
wl_got = []
wl_missed = []

q = ["Where is "]

c = 0
for loc in all_locs:
    res = geo.geoparse("%s%s" % (q,loc))
    if res:
        wl_got.append(loc)
    else:
        wl_missed.append(loc)
    c += 1

    if c % 1000 == 0:
        print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000 records
C

In [42]:
# Try Individual Locations (lowercase with context)
wl_got = []
wl_missed = []

q = ["Where is "]

c = 0
for loc in all_locs:
    loc = loc.lower()
    res = geo.geoparse("%s%s" % (q,loc))
    if res:
        wl_got.append(loc)
    else:
        wl_missed.append(loc)
    c += 1

    if c % 1000 == 0:
        print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000 records
C

In [39]:
# Try Individual Locations (lowercase)
wl_got = []
wl_missed = []

c = 0
for loc in all_locs:
    loc = loc.lower()
    res = geo.geoparse("%s" % (loc))
    if res:
        wl_got.append(loc)
    else:
        wl_missed.append(loc)
    c += 1

    if c % 1000 == 0:
        print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000 records
C

In [5]:
# Random Context Experiments

sample_queries = ['What time did the flight T2345G land in {}',
                  'Where in {} did ship T33442 dock in March of 2016',
                  'Who was the most powerful leader in {} in the year 2018',
                  'What is the most common religion practiced in {}',
                  'Who took down flight T2345G in {} in the year 1956',
                  'What is the population in {} currently',
                  'What was the death toll in {} in 2009',
                  'Who was the pilot on flight T2345G when the plane crashed in {} in 1999',
                  'Where in {} did the flight T2345G crash',
                  'Who is the richest person living in {} currently',
                  'What time did ship T2345G arrive in {} last Friday',
                  'Who was the first person born in {} in 2008',
                  'What was the average salary in {} last year',
                  'What is currently the most high paying job in {}',
                  'What was the most high paying job in {} in 1995',
                  'What is adjacent to {}',
                  'How many children were born in {} in 2016',
                  'What is the unemployment rate in {} right now',
                  'What is {}',
                  'What language do the people in {} speak',
                  'Where did ship {} sail to in 2016']

In [8]:
# Individual Uppercase with Random Context
import random
l_got = []
l_missed = []

c = 0
for loc in all_locs:
    v = random.randint(0,len(sample_queries)-1)
    res = geo.geoparse(sample_queries[v].format(loc))
    if res:
        l_got.append(sample_queries[v].format(loc))
    else:
        l_missed.append(sample_queries[v].format(loc))
    c += 1

    if c % 1000 == 0:
        print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(l_got), c))
print("%s/%s missed" % (len(l_missed), c))

Completed 1000 records
Completed 2000 records
Completed 3000 records
Completed 4000 records
Completed 5000 records
Completed 6000 records
Completed 7000 records
Completed 8000 records
Completed 9000 records
Completed 10000 records
Completed 11000 records
Completed 12000 records
Completed 13000 records
Completed 14000 records
Completed 15000 records
Completed 16000 records
Completed 17000 records
Completed 18000 records
Completed 19000 records
Completed 20000 records
Completed 21000 records
Completed 22000 records
Completed 23000 records
Completed 24000 records
Completed 25000 records
Completed 26000 records
Completed 27000 records
Completed 28000 records
Completed 29000 records
Completed 30000 records
Completed 31000 records
Completed 32000 records
Completed 33000 records
Completed 34000 records
Completed 35000 records
Completed 36000 records
Completed 37000 records
Completed 38000 records
Completed 39000 records
Completed 40000 records
Completed 41000 records
Completed 42000 records
C

In [12]:
for l in l_got:
    print(l)

What was the most high paying job in Afghanistan in 1995
What time did ship T2345G arrive in Albania last Friday
What is currently the most high paying job in Algeria
Where in American Samoa did ship T33442 dock in March of 2016
What is adjacent to Andorra
What was the death toll in Angola in 2009
Who took down flight T2345G in Anguilla in the year 1956
Who was the pilot on flight T2345G when the plane crashed in Antarctica in 1999
What was the death toll in Antigua And Barbuda in 2009
Who was the pilot on flight T2345G when the plane crashed in Argentina in 1999
What is currently the most high paying job in Armenia
What language do the people in Aruba speak
Who was the most powerful leader in Australia in the year 2018
Who took down flight T2345G in Austria in the year 1956
What was the death toll in Azerbaijan in 2009
What time did ship T2345G arrive in Bahamas The last Friday
What is the most common religion practiced in Bahrain
What is the unemployment rate in Bangladesh right now


What is the population in Bedfordshire currently
What is the population in Belfast currently
What is adjacent to Berkshire
What is the most common religion practiced in Birmingham
What is the unemployment rate in Brechin right now
Where in Bridgnorth did ship T33442 dock in March of 2016
Where in Bristol did the flight T2345G crash
Where in Buckinghamshire did ship T33442 dock in March of 2016
What time did the flight T2345G land in Cambridge
How many children were born in Cambridgeshire in 2016
What language do the people in Channel Islands speak
What is the unemployment rate in Cleveland right now
Who was the first person born in Conwy in 2008
What is the population in Cornwall currently
What time did ship T2345G arrive in Coventry last Friday
Where in Cumbria did ship T33442 dock in March of 2016
Who was the pilot on flight T2345G when the plane crashed in Denbighshire in 1999
What was the average salary in Derby last year
What time did the flight T2345G land in Derbyshire
What time

What is adjacent to Melagaram
Who was the first person born in Melanattam in 2008
What was the death toll in Melattur in 2009
What was the most high paying job in Melpattampakkam in 1995
What was the most high paying job in Mettupalayam in 1995
Who is the richest person living in Mettur currently
How many children were born in Meyyanur in 2016
Who is the richest person living in Milavittan currently
What language do the people in Minakshipuram speak
What is the unemployment rate in Minambakkam right now
What time did the flight T2345G land in Minjur
Who was the most powerful leader in Modakurichi in the year 2018
What was the average salary in Mohanur last year
Who is the richest person living in Mopperipalayam currently
How many children were born in Mulagumudu in 2016
What time did ship T2345G arrive in Mulanur last Friday
What is Muthur
What was the death toll in Muttayyapuram in 2009
What was the death toll in Muvarasampettai in 2009
What was the death toll in Naduvattam in 2009
Wh

What was the average salary in Xhobe last year
What language do the people in Bethel speak
How many children were born in Ditlharapa in 2016
What was the average salary in Gamajalela last year
Who was the pilot on flight T2345G when the plane crashed in Gasita in 1999
Who was the most powerful leader in Gathwane in the year 2018
How many children were born in Gopong in 2016
What is the unemployment rate in Hebron right now
What time did ship T2345G arrive in Itholoke last Friday
What is the most common religion practiced in Kanaku
Who was the pilot on flight T2345G when the plane crashed in Kangwe in 1999
What is the unemployment rate in Kgoro right now
What was the death toll in Kokong in 2009
Who took down flight T2345G in Lejwana in the year 1956
Where in Leporung did the flight T2345G crash
What was the average salary in Lorwana last year
Where in Lotlhakane West did the flight T2345G crash
How many children were born in Mabutsane in 2016
What was the death toll in Magoriapitse in 

What was the most high paying job in Santa Rosa de Viterbo in 1995
Who took down flight T2345G in Santa Sofia in the year 1956
What language do the people in Sativasur speak
Where in Socota did ship T33442 dock in March of 2016
What was the average salary in Somondoco last year
What is the most common religion practiced in Susacon
What was the death toll in Sutamarchan in 2009
What is the population in Tibasosa currently
Where in Tinjaca did the flight T2345G crash
What time did the flight T2345G land in Tipacoque
Who is the richest person living in Tota currently
How many children were born in Tunungua in 2016
How many children were born in Tutasa in 2016
What is adjacent to Umbita
Who took down flight T2345G in Viracacha in the year 1956
Who was the first person born in Zetaquira in 2008
How many children were born in Aguadas in 2016
Where in Chinchina did the flight T2345G crash
What is currently the most high paying job in La Dorada
Who was the most powerful leader in La Merced in 

...

What was the death toll in Amuzgos in 2009
What time did ship T2345G arrive in Asuncion Nochixtlan last Friday
What is adjacent to Atempa
What was the most high paying job in Ayoquezco in 1995
What is the population in Ayotzintepec currently
Where in Cacaotepec did the flight T2345G crash
What time did the flight T2345G land in Chiltepec
How many children were born in Coyotepec in 2016
What is adjacent to Crucecita
What is the unemployment rate in Cuicatlan right now
Who was the most powerful leader in Ejutla de Crespo in the year 2018
What was the death toll in Fraccionamiento el Rosario in 2009
What language do the people in Huatulco speak
Where in Huautla did the flight T2345G crash
What time did ship T2345G arrive in Huaxpaltepec last Friday
Who took down flight T2345G in Ingenio in the year 1956
Who was the pilot on flight T2345G when the plane crashed in Ixcatlan in 1999
Where did ship Ixhuatan sail to in 2016
What time did the flight T2345G land in Ixtepec
Who took down flight T

What is the population in Dealu currently
How many children were born in Feliceni in 2016
How many children were born in Frumoasa in 2016
What is the unemployment rate in Lazarea right now
What is the population in Mihaileni currently
How many children were born in Ocland in 2016
What language do the people in Plaiesii-de-Jos speak
What was the death toll in Toplita in 2009
What is the population in Tusnad currently
What time did ship T2345G arrive in Ulies last Friday
What is the population in Vlahita currently
Where in Zetea did ship T33442 dock in March of 2016
Who is the richest person living in Aninoasa currently
What time did the flight T2345G land in Baia de Cris
What time did ship T2345G arrive in Banita last Friday
What is adjacent to Beriu
Who took down flight T2345G in Berthelot in the year 1956
Who is the richest person living in Bosorod currently
What time did the flight T2345G land in Branisca
What is the population in Buces currently
What is the population in Bucuresci c

What was the death toll in Yunak in 2009
Who was the pilot on flight T2345G when the plane crashed in Dumlupinar in 1999
What is currently the most high paying job in Gediz
What is adjacent to Kutahya
Who is the richest person living in Pazarlar currently
What time did ship T2345G arrive in Arguvan last Friday
Where in Dogansehir did the flight T2345G crash
Who was the pilot on flight T2345G when the plane crashed in Doganyol in 1999
Who was the most powerful leader in Hekimhan in the year 2018
What language do the people in Kale speak
Who was the first person born in Yazihan in 2008
What is the most common religion practiced in Ahmetli
What was the death toll in Demirci in 2009
Where did ship Kirkagac sail to in 2016
How many children were born in Koprubasi in 2016
Who took down flight T2345G in Kula in the year 1956
Who was the pilot on flight T2345G when the plane crashed in Manisa in 1999
What language do the people in Saruhanli speak
How many children were born in Selendi in 2016


What is adjacent to Leavenworth
Who was the first person born in Leawood in 2008
What is currently the most high paying job in Lenexa
Who was the most powerful leader in Manhattan in the year 2018
What language do the people in Minneapolis speak
What is currently the most high paying job in Moscow
What time did the flight T2345G land in Nashville
Who was the most powerful leader in Newton in the year 2018
Where in Olathe did ship T33442 dock in March of 2016
Where in Ottawa did the flight T2345G crash
What is Overland Park
Who was the pilot on flight T2345G when the plane crashed in Parsons in 1999
Who was the most powerful leader in Pittsburg in the year 2018
Who was the first person born in Prairie Village in 2008
What was the most high paying job in Rose Hill in 1995
What was the most high paying job in Salina in 1995
What is adjacent to Shawnee
What is Topeka
What was the most high paying job in Wichita in 1995
What is adjacent to Albany
What was the death toll in Ashland in 2009
W

What is the most common religion practiced in Niskayuna
Who was the most powerful leader in North Castle in the year 2018
What time did ship T2345G arrive in North Greenbush last Friday
What was the most high paying job in North Hempstead in 1995
Who was the first person born in North Syracuse in 2008
What is adjacent to North Tonawanda
What was the average salary in Northport last year
What is the most common religion practiced in Norwich
Who is the richest person living in Nyack currently
What was the average salary in Ogden last year
What was the death toll in Ogdensburg in 2009
What is the population in Olean currently
What was the most high paying job in Oneida in 1995
What is Oneonta
Where did ship Onondaga sail to in 2016
Who was the pilot on flight T2345G when the plane crashed in Ontario in 1999
What is the unemployment rate in Orchard Park right now
What time did ship T2345G arrive in Ossining last Friday
Who was the first person born in Oswego in 2008
Who was the pilot on fl

In [13]:
for l in l_missed:
    print(l)

What time did ship T2345G arrive in Christmas Island last Friday
What time did ship T2345G arrive in Cook Islands last Friday
What is the unemployment rate in Man (Isle of) right now
What is Montserrat
How many children were born in Palestinian Territory Occupied in 2016
What is currently the most high paying job in Sierra Leone
Who was the pilot on flight T2345G when the plane crashed in Tajikistan in 1999
Who was the first person born in Tokelau in 2008
Where did ship United Arab Emirates sail to in 2016
Who was the most powerful leader in United States Minor Outlying Islands in the year 2018
What is adjacent to Andhra Pradesh
What is Assam
Where did ship Haryana sail to in 2016
How many children were born in Kenmore in 2016
Where in Lakshadweep did ship T33442 dock in March of 2016
What language do the people in Maharashtra speak
What is the most common religion practiced in Telangana
What time did the flight T2345G land in Vaishali
What is Bamiyan
How many children were born in Far

What is Mongra
What language do the people in Nailajanjgir speak
Who took down flight T2345G in Namna Kalan in the year 1956
What is Pandariya
What is adjacent to Phunderdihari
What is the unemployment rate in Raigarh right now
What is Saraipali
What is Simga
What was the death toll in Telgaon in 2009
Who is the richest person living in Tildanewra currently
What is Urla
Who was the pilot on flight T2345G when the plane crashed in Amli in 1999
What was the most high paying job in Altinho in 1995
What time did the flight T2345G land in Arpora
What was the death toll in Bambolim in 2009
What time did ship T2345G arrive in Bandora last Friday
Where in Bardez did the flight T2345G crash
What was the most high paying job in Benaulim in 1995
Where did ship Betora sail to in 2016
Who was the pilot on flight T2345G when the plane crashed in Bicholim in 1999
Who took down flight T2345G in Calapor in the year 1956
What time did ship T2345G arrive in Candolim last Friday
What is Caranzalem
What is

What was the death toll in Thirunirmalai in 2009
What time did the flight T2345G land in Thiruparankundram
What is the population in Thiruparappu currently
What is adjacent to Thirupuvanam
What is Thiruvaivaru
Who was the pilot on flight T2345G when the plane crashed in Thiruvenkatam in 1999
Where in Thiruvennainallur did ship T33442 dock in March of 2016
Who is the richest person living in Thiruvithankodu currently
Who was the first person born in Thisayanvilai in 2008
Where did ship Thittacheri sail to in 2016
What is the population in Thottipalayam currently
Where did ship Thottiyam sail to in 2016
Who was the pilot on flight T2345G when the plane crashed in Thudiyalur in 1999
Who is the richest person living in Thuthipattu currently
What time did the flight T2345G land in Thuvakudi
What language do the people in Tindivanam speak
What time did ship T2345G arrive in Tiruchchendur last Friday
Where in Tiruchengode did the flight T2345G crash
What is the unemployment rate in Tirukkattu

Where did ship Boutersem sail to in 2016
What is adjacent to Diest
What language do the people in Dilbeek speak
Where in Drogenbos did the flight T2345G crash
Who took down flight T2345G in Galmaarden in the year 1956
What is the most common religion practiced in Geetbets
What is currently the most high paying job in Glabbeek
What is Gooik
Where in Grimbergen did the flight T2345G crash
What was the death toll in Haacht in 2009
Where did ship Hoegaarden sail to in 2016
Who was the pilot on flight T2345G when the plane crashed in Holsbeek in 1999
Where in Kampenhout did ship T33442 dock in March of 2016
What was the average salary in Keerbergen last year
What is Kraainem
What was the most high paying job in Lennik in 1995
What is Linter
Who is the richest person living in Londerzeel currently
Who was the most powerful leader in Machelen in the year 2018
What time did ship T2345G arrive in Meise last Friday
Who was the most powerful leader in Opwijk in the year 2018
Where in Oud-Heverlee

What is the most common religion practiced in Caldono
What is the most common religion practiced in Caloto
What is the population in El Bordo currently
What is the most common religion practiced in El Tambo
What is the unemployment rate in La Sierra right now
Where did ship Lopez sail to in 2016
What was the average salary in Mercaderes last year
Where in Morales did ship T33442 dock in March of 2016
What is Padilla
Where in Piamonte did the flight T2345G crash
What is the most common religion practiced in Popayan
What time did ship T2345G arrive in Purace last Friday
Who took down flight T2345G in Rosas in the year 1956
What is Santander de Quilichao
Who took down flight T2345G in Silvia in the year 1956
What is Suarez
What is Timbio
Who took down flight T2345G in Timbiqui in the year 1956
Where in Toribio did ship T33442 dock in March of 2016
What was the death toll in Totoro in 2009
What is the most common religion practiced in Aguachica
What is the unemployment rate in Agustin Coda

...

Who was the most powerful leader in Mihama in the year 2018
What is adjacent to Miwa
How many children were born in Nagakute in 2016
What is currently the most high paying job in Nishiharu
What is Nisshin
Who was the pilot on flight T2345G when the plane crashed in Oharu in 1999
What is the most common religion practiced in Owariashi
What is the most common religion practiced in Saori
Who was the most powerful leader in Shinshiro in the year 2018
Who was the pilot on flight T2345G when the plane crashed in Shippo in 1999
What is the unemployment rate in Takahama right now
Where in Taketoyo did ship T33442 dock in March of 2016
What is Tokai
What time did ship T2345G arrive in Tokoname last Friday
What was the most high paying job in Toyoake in 1995
What was the most high paying job in Toyohashi in 1995
Who was the first person born in Toyota in 2008
Who took down flight T2345G in Tsushima in the year 1956
What is the unemployment rate in Yatomi right now
What time did ship T2345G arriv

What is adjacent to Boueni
What is the population in Chiconi currently
What was the death toll in Chirongui in 2009
What is the most common religion practiced in Ouangani
Where did ship Sada sail to in 2016
Who was the most powerful leader in Tsingoni in the year 2018
What was the death toll in Dzaoudzi in 2009
Where in Pamanzi did ship T33442 dock in March of 2016
Who took down flight T2345G in Calvillo in the year 1956
What time did ship T2345G arrive in Margaritas last Friday
Who was the first person born in Pabellon de Arteaga in 2008
What was the most high paying job in Pabellon de Hidalgo in 1995
What is Becal
How many children were born in Calkini in 2016
Where in Carmen did ship T33442 dock in March of 2016
Who was the most powerful leader in Champoton in the year 2018
Who is the richest person living in Escarcega currently
What was the death toll in Hecelchakan in 2009
Who took down flight T2345G in Hopelchen in the year 1956
What is the population in Nunkini currently
Where i

What is currently the most high paying job in Sepolno Krajenskie
What is currently the most high paying job in Solec Kujawski
What is currently the most high paying job in Wloclawek
Who was the most powerful leader in Aleksandrow Lodzki in the year 2018
What time did the flight T2345G land in Belchatow
Who was the first person born in Bratoszewice in 2008
Who was the pilot on flight T2345G when the plane crashed in Brzeziny in 1999
Who is the richest person living in Glowno currently
What was the most high paying job in Koluszki in 1995
Where in Konstantynow Lodzki did ship T33442 dock in March of 2016
What was the most high paying job in Lask in 1995
What is the most common religion practiced in Opoczno
What is adjacent to Pabianice
Where did ship Piotrkow Trybunalski sail to in 2016
What language do the people in Radomsko speak
What is the unemployment rate in Rawa Mazowiecka right now
Who is the richest person living in Tomaszow Mazowiecki currently
What is the population in Tuszyn 

What is the unemployment rate in Kartaly right now
Who was the most powerful leader in Lokomotivnyj in the year 2018
Where did ship Magnitka sail to in 2016
Who is the richest person living in Miass currently
Where did ship Minjar sail to in 2016
What was the most high paying job in Novosineglazovskij in 1995
What is Ozjorsk
Who was the pilot on flight T2345G when the plane crashed in Plast in 1999
What is the population in Roza currently
What time did ship T2345G arrive in Suleja last Friday
Who is the richest person living in Trjohgornij currently
What is the unemployment rate in Ust-Katav right now
Who was the first person born in Verhneuralsk in 2008
What language do the people in Verhnij Ufalej speak
What is adjacent to Atamanovka
What is adjacent to Balej
What was the average salary in Bukachacha last year
Who took down flight T2345G in Chernyshevsk in the year 1956
Who was the most powerful leader in Darasun in the year 2018
What is adjacent to Gornyy
Who took down flight T2345G

What is adjacent to Kulp
What language do the people in Lice speak
What is adjacent to Silvan
What is Cumayeri
What is Duzce
Who is the richest person living in Gumusova currently
What is Kaynasli
Who is the richest person living in Edirne currently
What is the most common religion practiced in Enez
What is the population in Havsa currently
Where in Meric did ship T33442 dock in March of 2016
What language do the people in Uzunkopru speak
What is the population in Agin currently
What was the average salary in Alacakaya last year
What was the average salary in Aricak last year
What time did ship T2345G arrive in Baskil last Friday
What is adjacent to Elazig
How many children were born in Keban in 2016
What is the unemployment rate in Maden right now
Where in Sivrice did ship T33442 dock in March of 2016
What is currently the most high paying job in Erzincan
Where in Ilic did the flight T2345G crash
Where did ship Kemaliye sail to in 2016
Who was the most powerful leader in Refahiye in t

In [14]:
# World Locations Upperrcase with Random Context

wl_got = []
wl_missed = []

c = 0
with open("../Rasa/roger_nlu/location_data/world_locations_ed2.txt", 'r') as wlf:
    print("file open")
    line = wlf.readline()
    while line:
        #random number
        v = random.randint(0,len(sample_queries)-1)
        res = geo.geoparse(sample_queries[v].format(line.strip()))
        if res:
            wl_got.append(sample_queries[v].format(line.strip()))
        else:
            wl_missed.append(sample_queries[v].format(line.strip()))
        line = wlf.readline()
        c += 1
        
#         if c % 1000 == 0:
#             print("Completed %s records" % c)

# Done!
print("Finally Done!")
print("%s/%s achieved" % (len(wl_got), c))
print("%s/%s missed" % (len(wl_missed), c))

file open
Finally Done!
42040/52709 achieved
10669/52709 missed


In [15]:
for wl in wl_got:
    print(wl)

What was the average salary in Afghanistan last year
What time did ship T2345G arrive in Albania last Friday
What is adjacent to Algeria
What was the average salary in American Samoa last year
What is the population in Andorra currently
Who was the pilot on flight T2345G when the plane crashed in Angola in 1999
How many children were born in Anguilla in 2016
What language do the people in Antarctica speak
What was the average salary in Antigua And Barbuda last year
What is the unemployment rate in Argentina right now
What time did the flight T2345G land in Armenia
What is adjacent to Aruba
Where in Australia did ship T33442 dock in March of 2016
What is Austria
What language do the people in Azerbaijan speak
Where in Bahamas The did the flight T2345G crash
Who was the pilot on flight T2345G when the plane crashed in Bahrain in 1999
What is adjacent to Bangladesh
Who took down flight T2345G in Barbados in the year 1956
Who was the pilot on flight T2345G when the plane crashed in Belarus

What time did the flight T2345G land in Edappal, Kerala
What is Edathala, Kerala
How many children were born in Elayavur, Kerala in 2016
Where in Elur, Kerala did ship T33442 dock in March of 2016
Who is the richest person living in Eranholi, Kerala currently
What is the unemployment rate in Erattupetta, Kerala right now
What is currently the most high paying job in Ernakulam, Kerala
Who was the pilot on flight T2345G when the plane crashed in Eruvatti, Kerala in 1999
Who is the richest person living in Ettumanoor, Kerala currently
What is currently the most high paying job in Feroke, Kerala
Who was the pilot on flight T2345G when the plane crashed in Guruvayur, Kerala in 1999
What is the population in Haripad, Kerala currently
What was the average salary in Hosabettu, Kerala last year
Who was the most powerful leader in Idukki, Kerala in the year 2018
Who was the first person born in Iringaprom, Kerala in 2008
What is the population in Irinjalakuda, Kerala currently
What was the avera

Who was the first person born in Srivilliputtur, Tamil Nadu in 2008
Who was the most powerful leader in Suchindram, Tamil Nadu in the year 2018
What is Suliswaranpatti, Tamil Nadu
Who was the pilot on flight T2345G when the plane crashed in Sulur, Tamil Nadu in 1999
What is adjacent to Surampatti, Tamil Nadu
What is currently the most high paying job in Suriyampalayam, Tamil Nadu
What was the average salary in Swamimalai, Tamil Nadu last year
What is adjacent to Tambaram, Tamil Nadu
Where did ship Tattayyangarpettai, Tamil Nadu sail to in 2016
Who is the richest person living in Tayilupatti, Tamil Nadu currently
What was the most high paying job in Tenkasi, Tamil Nadu in 1995
What is the most common religion practiced in Thakkolam, Tamil Nadu
What was the average salary in Thamaraikulam, Tamil Nadu last year
What was the average salary in Thanjavur, Tamil Nadu last year
Where in Thanthoni, Tamil Nadu did ship T33442 dock in March of 2016
Where in Tharangambadi, Tamil Nadu did the fligh

Where in Molendinar, Queensland did ship T33442 dock in March of 2016
Who was the pilot on flight T2345G when the plane crashed in Moranbah, Queensland in 1999
Where in Morayfield, Queensland did ship T33442 dock in March of 2016
How many children were born in Mossman, Queensland in 2016
What is the population in Mount Glorious, Queensland currently
Who took down flight T2345G in Mount Isa, Queensland in the year 1956
Who took down flight T2345G in Murarrie, Queensland in the year 1956
Who was the pilot on flight T2345G when the plane crashed in Nairand Kay, Queensland in 1999
What language do the people in Nambour, Queensland speak
What is the unemployment rate in Nerang, Queensland right now
What was the death toll in Nobby Beach, Queensland in 2009
What time did ship T2345G arrive in Noosa Heads, Queensland last Friday
What is Noosaville, Queensland
What is the most common religion practiced in Paddington, Queensland
What language do the people in Port Douglas, Queensland speak
What

How many children were born in Guarai, Tocantins in 2016
Who was the most powerful leader in Gurupi, Tocantins in the year 2018
What was the most high paying job in Miracema Do Tocantins, Tocantins in 1995
What was the most high paying job in Palmas, Tocantins in 1995
Who was the most powerful leader in Paraiso, Tocantins in the year 2018
What is the most common religion practiced in Parana, Tocantins
How many children were born in Sitio Novo Do Tocantins, Tocantins in 2016
What was the death toll in Taguatinga, Tocantins in 2009
What is currently the most high paying job in Xambioa, Tocantins
Who took down flight T2345G in Seria, Belait in the year 1956
How many children were born in Bandar Seri Begawan, Brunei-muara in 2016
What was the death toll in Tutong, Tutong in 2009
Who was the pilot on flight T2345G when the plane crashed in Bansko, Blagoevgrad in 1999
Where in Hadzhidimovo, Blagoevgrad did the flight T2345G crash
Where in Jakoruda, Blagoevgrad did the flight T2345G crash
Whe

...

What time did ship T2345G arrive in Basciftlik, Tokat last Friday
What is the population in Pazar, Tokat currently
Who was the most powerful leader in Resadiye, Tokat in the year 2018
What is currently the most high paying job in Tokat, Tokat
What is the most common religion practiced in Turhal, Tokat
What is the unemployment rate in Yesilyurt, Tokat right now
What is the most common religion practiced in Zile, Tokat
Who was the pilot on flight T2345G when the plane crashed in Arakli, Trabzon in 1999
What is the population in Arsin, Trabzon currently
What time did ship T2345G arrive in Besikduzu, Trabzon last Friday
Where did ship Caykara, Trabzon sail to in 2016
What was the most high paying job in Dernekpazari, Trabzon in 1995
What time did the flight T2345G land in Hayrat, Trabzon
What was the death toll in Koprubasi, Trabzon in 2009
What is Macka, Trabzon
Who is the richest person living in Of, Trabzon currently
Where in Salpazari, Trabzon did the flight T2345G crash
Where in Surme

What is the most common religion practiced in Hobe Sound, Florida
What language do the people in Holiday, Florida speak
Who was the first person born in Holly Hill, Florida in 2008
Who is the richest person living in Hollywood, Florida currently
Where did ship Homestead, Florida sail to in 2016
What was the most high paying job in Homosassa, Florida in 1995
What is Hudson, Florida
What is the most common religion practiced in Immokalee, Florida
Where in Inverness, Florida did the flight T2345G crash
Who took down flight T2345G in Iona, Florida in the year 1956
How many children were born in Ives Estates, Florida in 2016
What time did ship T2345G arrive in Jacksonville, Florida last Friday
What was the most high paying job in Jacksonville Beach, Florida in 1995
What was the average salary in Jasmine Estates, Florida last year
Where in Jensen Beach, Florida did ship T33442 dock in March of 2016
Where did ship Jupiter, Florida sail to in 2016
What is adjacent to Kendale Lakes, Florida
Wha

Who was the pilot on flight T2345G when the plane crashed in Corry, Pennsylvania in 1999
Who is the richest person living in Cranberry Township, Pennsylvania currently
Where did ship Cresco, Pennsylvania sail to in 2016
What language do the people in Croydon, Pennsylvania speak
What language do the people in Dallas, Pennsylvania speak
Who was the most powerful leader in Dallastown, Pennsylvania in the year 2018
What is currently the most high paying job in Darby, Pennsylvania
Where in Darby Township, Pennsylvania did the flight T2345G crash
Who was the first person born in Downingtown, Pennsylvania in 2008
Who was the first person born in Drexel Hill, Pennsylvania in 2008
Where in Duncansville, Pennsylvania did ship T33442 dock in March of 2016
What was the average salary in Dunmore, Pennsylvania last year
What time did ship T2345G arrive in East Norriton, Pennsylvania last Friday
What is adjacent to East Stroudsburg, Pennsylvania
What language do the people in Easton, Pennsylvania spe

How many children were born in Sikkim, India in 2016
What is currently the most high paying job in Tamil Nadu, India
What time did ship T2345G arrive in Telangana, India last Friday
Where did ship Tripura, India sail to in 2016
What is the most common religion practiced in Uttar Pradesh, India
What is currently the most high paying job in Uttarakhand, India
What time did the flight T2345G land in Vaishali, India
What time did ship T2345G arrive in West Bengal, India last Friday
Who took down flight T2345G in Badakhshan, Afghanistan in the year 1956
What is currently the most high paying job in Badgis, Afghanistan
Who was the pilot on flight T2345G when the plane crashed in Baglan, Afghanistan in 1999
How many children were born in Balkh, Afghanistan in 2016
How many children were born in Bamiyan, Afghanistan in 2016
Who was the pilot on flight T2345G when the plane crashed in Farah, Afghanistan in 1999
What language do the people in Faryab, Afghanistan speak
Where in Gawr, Afghanistan 

What is currently the most high paying job in Oshikoto, Namibia
What language do the people in Otjozondjupa, Namibia speak
What was the average salary in Yaren, Nauru last year
Where in Bagmati, Nepal did the flight T2345G crash
What was the most high paying job in Bheri, Nepal in 1995
Who is the richest person living in Dhawalagiri, Nepal currently
What language do the people in Gandaki, Nepal speak
Who was the most powerful leader in Janakpur, Nepal in the year 2018
How many children were born in Karnali, Nepal in 2016
What is the most common religion practiced in Koshi, Nepal
What is currently the most high paying job in Lumbini, Nepal
What is currently the most high paying job in Mahakali, Nepal
Who was the pilot on flight T2345G when the plane crashed in Mechi, Nepal in 1999
Where in Narayani, Nepal did ship T33442 dock in March of 2016
Where did ship Rapti, Nepal sail to in 2016
What time did ship T2345G arrive in Sagarmatha, Nepal last Friday
What was the average salary in Seti,

In [17]:
for missed in wl_missed:
    print(missed)

Who took down flight T2345G in Christmas Island in the year 1956
What is the unemployment rate in External Territories Of Australia right now
What was the death toll in Heard And Mcdonald Islands in 2009
What is currently the most high paying job in Man (isle Of)
What is the most common religion practiced in Palestinian Territory Occupied
What was the most high paying job in Reunion in 1995
What is adjacent to Sao Tome And Principe
Who was the most powerful leader in Sierra Leone in the year 2018
Where did ship Suriname sail to in 2016
What is the unemployment rate in Tajikistan right now
What is the most common religion practiced in Tokelau
Who was the most powerful leader in United States Minor Outlying Islands in the year 2018
What was the average salary in Addanki, Andhra Pradesh last year
Where in Bobbili, Andhra Pradesh did ship T33442 dock in March of 2016
Where in Bommuru, Andhra Pradesh did the flight T2345G crash
What is Chatakonda, Andhra Pradesh
Who was the most powerful le

What is adjacent to Sogamoso, Boyaca
What was the death toll in Somondoco, Boyaca in 2009
What is the most common religion practiced in Soraca, Boyaca
Where in Sotaquira, Boyaca did the flight T2345G crash
Where did ship Susacon, Boyaca sail to in 2016
What was the average salary in Sutatenza, Boyaca last year
What was the most high paying job in Tasco, Boyaca in 1995
What is currently the most high paying job in Tenza, Boyaca
Who was the most powerful leader in Tibana, Boyaca in the year 2018
What is the unemployment rate in Toca, Boyaca right now
What language do the people in Togui, Boyaca speak
Who took down flight T2345G in Topaga, Boyaca in the year 1956
What was the most high paying job in Tota, Boyaca in 1995
Where did ship Tunja, Boyaca sail to in 2016
Who was the first person born in Turmeque, Boyaca in 2008
What time did the flight T2345G land in Tuta, Boyaca
What is the unemployment rate in Ventaquemada, Boyaca right now
What is the unemployment rate in Aranzazu, Caldas rig

What language do the people in Spalt, Bayern speak
Where did ship Stadtbergen, Bayern sail to in 2016
What was the most high paying job in Staffelstein, Bayern in 1995
What is the population in Stein, Bayern currently
What was the most high paying job in Thansau, Bayern in 1995
What is the most common religion practiced in Traunreut, Bayern
What is the unemployment rate in Treuchtlingen, Bayern right now
What time did ship T2345G arrive in Unterbergen, Bayern last Friday
What is Unterhaching, Bayern
How many children were born in Veitshochheim, Bayern in 2016
What is Viechtach, Bayern
Where in Vilgertshofen, Bayern did ship T33442 dock in March of 2016
What was the most high paying job in Vilshofen, Bayern in 1995
What is adjacent to Volkach, Bayern
What was the most high paying job in Waldkraiburg, Bayern in 1995
Who was the most powerful leader in Walkertshofen, Bayern in the year 2018
Who took down flight T2345G in Weibenhorn, Bayern in the year 1956
Who took down flight T2345G in W

What is currently the most high paying job in Rollingen, Mersch
What is the unemployment rate in Scherfenhof, Mersch right now
What language do the people in Schiltzberg, Mersch speak
What was the most high paying job in Schoenfels, Mersch in 1995
Who took down flight T2345G in Schoos, Mersch in the year 1956
Who was the first person born in Tuntange, Mersch in 2008
Who was the most powerful leader in Arsdorf, Redange in the year 2018
What is adjacent to Beckerich, Redange
Who is the richest person living in Bettborn, Redange currently
What was the death toll in Brattert-rindschleiden, Redange in 2009
How many children were born in Buschrodt, Redange in 2016
How many children were born in Calmus, Redange in 2016
What is the most common religion practiced in Colpach-bas, Redange
What was the death toll in Colpach-haut, Redange in 2009
What was the death toll in Ehner, Redange in 2009
What was the most high paying job in Ell, Redange in 1995
Where in Eltz, Redange did the flight T2345G c

What is currently the most high paying job in Varghis, Covasna
Where did ship Zagon, Covasna sail to in 2016
What is the unemployment rate in Baleni, Dambovita right now
What is Branesti, Dambovita
What was the most high paying job in Candesti, Dambovita in 1995
What time did ship T2345G arrive in Ciocanesti, Dambovita last Friday
What time did ship T2345G arrive in Cobia, Dambovita last Friday
What was the death toll in Cojasca, Dambovita in 2009
Who is the richest person living in Comisani, Dambovita currently
What is adjacent to Corbii Mari, Dambovita
What is the unemployment rate in Cornatelu, Dambovita right now
What is currently the most high paying job in Cornesti, Dambovita
What was the death toll in Costestii Din Vale, Dambovita in 2009
What time did ship T2345G arrive in Crangurile De Sus, Dambovita last Friday
What is the unemployment rate in Crevedia, Dambovita right now
Who was the pilot on flight T2345G when the plane crashed in Darmanesti, Dambovita in 1999
What is Dobra

Where in Canelones, Canelones did the flight T2345G crash
What is adjacent to Juan Antonio Artigas, Canelones
What was the average salary in Pando, Canelones last year
Where did ship Maldonado, Maldonado sail to in 2016
Where in Rivera, Rivera did the flight T2345G crash
What time did the flight T2345G land in Chuy, Rocha
Who was the pilot on flight T2345G when the plane crashed in Rocha, Rocha in 1999
Where did ship Dolores, Soriano sail to in 2016
What is the population in Mercedes, Soriano currently
Where did ship Paso De Los Toros, Tacuarembo sail to in 2016
Where in Tacuarembo, Tacuarembo did the flight T2345G crash
Where did ship Asaka, Andijon sail to in 2016
Who took down flight T2345G in Hakkulobod, Andijon in the year 1956
Who was the most powerful leader in Hocaobod, Andijon in the year 2018
Where in Honobod, Andijon did ship T33442 dock in March of 2016
Where did ship Kurgontepa, Andijon sail to in 2016
What language do the people in Paytug, Andijon speak
Where in Cangeldi,